周内效应——定投篇

In [1]:
import pandas as pd
from datetime import datetime
import trdb2py
import numpy as np

isStaticImg = False
width = 960
height = 768

pd.options.display.max_columns = None
pd.options.display.max_rows = None

trdb2cfg = trdb2py.loadConfig('./trdb2.yaml')

In [2]:
# 具体基金
asset = 'jqdata.000300_XSHG|1d'
# baselineasset = 'jrj.510310'
# asset = 'jrj.110011'
# baselineasset = 'jqdata.000300_XSHG|1d'

# 起始时间，0表示从最开始算起
tsStart = 0
tsStart = int(trdb2py.str2timestamp('2013-05-01', '%Y-%m-%d'))

# 结束时间，-1表示到现在为止
tsEnd = -1
tsEnd = int(trdb2py.str2timestamp('2020-12-31', '%Y-%m-%d'))

# 初始资金池
paramsinit = trdb2py.trading2_pb2.InitParams(
    money=10000,
)

# 买入参数，用全部的钱来买入（也就是复利）
paramsbuy = trdb2py.trading2_pb2.BuyParams(
    perHandMoney=1,
)

# # 买入参数，用全部的钱来买入（也就是复利）
# paramsbuy2 = trdb2py.trading2_pb2.BuyParams(
#     perHandMoney=1/6,
# )

# 买入参数，用全部的钱来买入（也就是复利）
paramsbuy2 = trdb2py.trading2_pb2.BuyParams(
    perHandMoney=0.5,
)

# 卖出参数，全部卖出
paramssell = trdb2py.trading2_pb2.SellParams(
    perVolume=1,
)

paramsaip = trdb2py.trading2_pb2.AIPParams(
    money=10000,
    type=trdb2py.trading2_pb2.AIPTT_MONTHDAY,
    day=1,
)

# 止盈参数，120%止盈
paramstakeprofit = trdb2py.trading2_pb2.TakeProfitParams(
    perVolume=1,
#     isOnlyProfit=True,
#     isFinish=True,
)

# 止盈参数，120%止盈
paramstakeprofit2 = trdb2py.trading2_pb2.TakeProfitParams(
    perVolume=1,
#     isOnlyProfit=True,
    isFinish=True,
)

# 止盈参数，120%止盈
paramstakeprofit1 = trdb2py.trading2_pb2.TakeProfitParams(
    perVolume=1,
    isOnlyProfit=True,
#     isFinish=True,
)

# 止盈参数，120%止盈
paramstakeprofit3 = trdb2py.trading2_pb2.TakeProfitParams(
    perVolume=1,
    isOnlyProfit=True,
    isFinish=True,
)

# 卖出参数，全部卖出
paramssell7 = trdb2py.trading2_pb2.SellParams(
#     perVolume=1,
    keepTime=7 * 24 * 60 * 60,
)

lststart = [1, 2, 3, 4, 5]
lsttitle = ['周一', '周二', '周三', '周四', '周五']

In [3]:
def calcweekday2val2(wday, offday):
    if offday == 1:
        if wday == 5:
            return 3
    if offday == 2:
        if wday >= 4:
            return 4
    if offday == 3:
        if wday >= 3:
            return 5
    if offday == 4:
        if wday >= 2:
            return 6
        
    return offday


def getAIPLastTs(pnl):
    ctrlnums = len(pnl.lstCtrl)

    if ctrlnums <= 0:
        return -1
    
    if pnl.lstCtrl[ctrlnums - 1].type == trdb2py.trading2_pb2.CTRL_SELL:
        return pnl.lstCtrl[ctrlnums - 1].ts
    
    return -1

def getLastResult(pnl) -> dict:
    nums = len(pnl.values)

    if nums <= 0:
        return None
    
    return {'cost': pnl.values[nums - 1].cost, 'value': pnl.values[nums - 1].value}

def getLastCtrl(pnl):
    ctrlnums = len(pnl.lstCtrl)

    if ctrlnums <= 0:
        return None
    
    return pnl.lstCtrl[ctrlnums - 1]


def getPNLValueWithTimestamp(ts, pnl: trdb2py.trading2_pb2.PNLAssetData) -> int:
    for i in range(0, len(pnl.values)):
        if ts == pnl.values[i].ts:
            return i

        if ts < pnl.values[i].ts:
            pnl.values.insert(i, trdb2py.trading2_pb2.PNLDataValue(ts=ts))

            return i

    pnl.values.append(trdb2py.trading2_pb2.PNLDataValue(ts=ts))

    return len(pnl.values) - 1

def mergePNL(lstpnl: list) -> trdb2py.trading2_pb2.PNLAssetData:
    pnl = trdb2py.trading2_pb2.PNLAssetData()

    for vpnl in lstpnl:
        v = vpnl['pnl']

        for cai in range(0, len(v.values)):
            di = getPNLValueWithTimestamp(v.values[cai].ts, pnl)
            pnl.values[di].value += v.values[cai].value
            pnl.values[di].cost += v.values[cai].cost

            if pnl.values[di].cost > 0:
                pnl.values[di].perValue = pnl.values[di].value / \
                    pnl.values[di].cost
            else:
                pnl.values[di].perValue = 1
                
#             pnl.values[di].perValue = 2

    return pnl

def getNextMonthDay1(ts):
    dt = datetime.utcfromtimestamp(ts)
    
    if dt.month == 12:
        return datetime(dt.year + 1, 1, 1).timestamp()
    
    return datetime(dt.year, dt.month + 1, 1).timestamp()


def rmPNLValuesWithTimestamp(ts, pnl: trdb2py.trading2_pb2.PNLAssetData):
    i = getPNLValueWithTimestamp(ts, pnl)
    pnl.values.extend(pnl.values[0:i+1])
    
    
def getPNLTimestampLowInMonth(pnl: trdb2py.trading2_pb2.PNLAssetData) -> list:
    ts = 0
    dt = None
    lastPerValue = 0
    arr = []

    for i in range(0, len(pnl.values)):
        v = pnl.values[i]

        if ts == 0:
            ts = v.ts
            dt = datetime.utcfromtimestamp(ts)
            lastPerValue = v.perValue
        else:
            cdt = datetime.utcfromtimestamp(v.ts)
            if dt.year == cdt.year and dt.month == cdt.month:
                if lastPerValue > v.perValue:
                    ts = v.ts
                    dt = cdt
                    lastPerValue = v.perValue

                if i == len(pnl.values) - 1:
                    arr.append(ts)
            else:
                arr.append(ts)

                ts = v.ts
                dt = cdt
                lastPerValue = v.perValue

    return arr


def getPNLTimestampHighInMonth(pnl: trdb2py.trading2_pb2.PNLAssetData) -> list:
    ts = 0
    dt = None
    lastPerValue = 0
    arr = []

    for i in range(0, len(pnl.values)):
        v = pnl.values[i]

        if ts == 0:
            ts = v.ts
            dt = datetime.utcfromtimestamp(ts)
            lastPerValue = v.perValue
        else:
            cdt = datetime.utcfromtimestamp(v.ts)
            if dt.year == cdt.year and dt.month == cdt.month:
                if lastPerValue < v.perValue:
                    ts = v.ts
                    dt = cdt
                    lastPerValue = v.perValue

                if i == len(pnl.values) - 1:
                    arr.append(ts)
            else:
                arr.append(ts)

                ts = v.ts
                dt = cdt
                lastPerValue = v.perValue

    return arr

In [4]:
asset = 'jrj.110011'
# asset = 'jqdata.000036_XSHG|1d'
# asset = 'jqdata.000032_XSHG|1d'
asset = 'jqdata.000300_XSHG|1d'

# baseline    
s0 = trdb2py.trading2_pb2.Strategy(
    name="normal",
    asset=trdb2py.str2asset(asset),         
)
        
buy0 = trdb2py.trading2_pb2.CtrlCondition(
    name='buyandhold',
)

paramsbuy = trdb2py.trading2_pb2.BuyParams(
    perHandMoney=1,
)

paramsinit = trdb2py.trading2_pb2.InitParams(
    money=10000,
)

s0.buy.extend([buy0])
s0.paramsBuy.CopyFrom(paramsbuy)
s0.paramsInit.CopyFrom(paramsinit)        
p0 = trdb2py.trading2_pb2.SimTradingParams(
    assets=[trdb2py.str2asset(asset)],
    startTs=tsStart,
    endTs=tsEnd,
    strategies=[s0],
    title='沪深300',
)  

pnlBaseline = trdb2py.simTrading(trdb2cfg, p0)
trdb2py.showPNL(pnlBaseline, toImg=isStaticImg, width=width, height=height)

In [5]:
lstparams = []

for i in range(1, 32):
    buy0 = trdb2py.trading2_pb2.CtrlCondition(
        name='monthdayex',
        vals=[i],
    )

    s0 = trdb2py.trading2_pb2.Strategy(
        name="normal",
        asset=trdb2py.str2asset(asset),
    )
    
#     paramsaip = trdb2py.trading2_pb2.AIPParams(
#         money=10000,
#         type=trdb2py.trading2_pb2.AIPTT_WEEKDAY,
#         day=1,
#     )

    s0.buy.extend([buy0])
    s0.paramsBuy.CopyFrom(paramsbuy)
    s0.paramsSell.CopyFrom(paramssell)
#     s0.paramsInit.CopyFrom(paramsinit)
    s0.paramsAIP.CopyFrom(paramsaip)
    lstparams.append(trdb2py.trading2_pb2.SimTradingParams(
        assets=[trdb2py.str2asset(asset)],
        startTs=tsStart,
        endTs=tsEnd,
        strategies=[s0],
        title='{}定投'.format(i),
    ))
 
lstaippnl = trdb2py.simTradings(trdb2cfg, lstparams)

trdb2py.showPNLs(lstaippnl + [pnlBaseline], toImg=isStaticImg, width=width, height=height)

我们看到不管是每个月的几号买入，最终其实都差异不大

In [6]:
dfpnl1b = trdb2py.buildPNLReport(lstaippnl + [pnlBaseline])

dfpnl1b[['title', 'maxDrawdown', 'maxDrawdownStart', 'maxDrawdownEnd', 'totalReturns', 'sharpe', 'annualizedReturns', 'annualizedVolatility', 'variance']].sort_values(by='totalReturns', ascending=False)

title  maxDrawdown maxDrawdownStart maxDrawdownEnd  totalReturns  \
31  沪深300     0.466961       2015-06-08     2016-01-28      2.087535   
30   31定投     0.445683       2015-06-08     2015-08-26      1.568582   
27   28定投     0.441192       2015-06-08     2015-08-26      1.566009   
26   27定投     0.441218       2015-06-08     2015-08-26      1.565847   
29   30定投     0.444034       2015-06-08     2015-08-26      1.565478   
0     1定投     0.449336       2015-06-08     2015-08-26      1.565161   
28   29定投     0.441713       2015-06-08     2015-08-26      1.564366   
25   26定投     0.441647       2015-06-08     2015-08-26      1.563656   
24   25定投     0.442747       2015-06-08     2015-08-26      1.561474   
8     9定投     0.448915       2015-06-08     2015-08-26      1.561136   
2     3定投     0.448017       2015-06-08     2015-08-26      1.560910   
7     8定投     0.448089       2015-06-08     2015-08-26      1.560437   
1     2定投     0.448808       2015-06-08     2015-08-26      1.560345   
6     7定投     0.448439       2015-06-08     2015-08-26      1.558561   
23   24定投     0.445507       2015-06-08     2015-08-26      1.557415   
5     6定投     0.448396       2015-06-08     2015-08-26      1.557208   
3     4定投     0.448760       2015-06-08     2015-08-26      1.556467   
9    10定投     0.449429       2015-06-08     2015-08-26      1.555699   
4     5定投     0.448482       2015-06-08     2015-08-26      1.555323   
22   23定投     0.445556       2015-06-08     2015-08-26      1.555171   
10   11定投     0.449633       2015-06-08     2015-08-26      1.555164   
14   15定投     0.448663       2015-06-08     2015-08-26      1.554378   
17   18定投     0.447914       2015-06-08     2015-08-26      1.554354   
16   17定投     0.449142       2015-06-08     2015-08-26      1.553390   
13   14定投     0.449128       2015-06-08     2015-08-26      1.553362   
21   22定投     0.445265       2015-06-08     2015-08-26      1.552930   
19   20定投     0.447472       2015-06-08     2015-08-26      1.552580   
11   12定投     0.449470       2015-06-08     2015-08-26      1.552027   
15   16定投     0.448402       2015-06-08     2015-08-26      1.551738   
18   19定投     0.447476       2015-06-08     2015-08-26      1.551643   
20   21定投     0.446690       2015-06-08     2015-08-26      1.551360   
12   13定投     0.449434       2015-06-08     2015-08-26      1.551297   

      sharpe  annualizedReturns  annualizedVolatility  variance  
31  0.482750           0.141903              0.231803  0.090168  
30  0.194179           0.074189              0.227570  0.040485  
27  0.196269           0.073854              0.223436  0.039181  
26  0.196067           0.073832              0.223558  0.038868  
29  0.193955           0.073784              0.225744  0.039864  
0   0.187450           0.073743              0.233358  0.041392  
28  0.193797           0.073639              0.225180  0.039828  
25  0.194510           0.073547              0.223878  0.038960  
24  0.192954           0.073262              0.224208  0.039254  
8   0.187496           0.073218              0.230499  0.040483  
2   0.185411           0.073188              0.232933  0.041054  
7   0.186890           0.073127              0.230759  0.040371  
1   0.184876           0.073114              0.233208  0.040917  
6   0.185212           0.072882              0.231528  0.040534  
23  0.190215           0.072732              0.224652  0.039199  
5   0.184089           0.072705              0.231980  0.040510  
3   0.183214           0.072609              0.232562  0.040765  
9   0.184725           0.072508              0.230117  0.040250  
4   0.182658           0.072459              0.232452  0.040704  
22  0.188724           0.072439              0.224875  0.039213  
10  0.184700           0.072439              0.229770  0.040403  
14  0.184861           0.072336              0.229015  0.039833  
17  0.185542           0.072333              0.228157  0.040400  
16  0.184858           0.072207            

In [7]:
lsthigh = getPNLTimestampHighInMonth(pnlBaseline['pnl'])
lstlow = getPNLTimestampLowInMonth(pnlBaseline['pnl'])

lstparams = []
lstpnl = []

tsStart = int(trdb2py.str2timestamp('2013-05-01', '%Y-%m-%d'))


buy0 = trdb2py.trading2_pb2.CtrlCondition(
    name='timestampex',
    int64Vals=lsthigh,
)

s0 = trdb2py.trading2_pb2.Strategy(
    name="normal",
    asset=trdb2py.str2asset(asset),
)

s0.buy.extend([buy0])
#     s0.takeprofit.extend([takeprofit0])
s0.paramsBuy.CopyFrom(paramsbuy)
#     s0.paramsSell.CopyFrom(paramssell)
#     s0.paramsTakeProfit.CopyFrom(paramstakeprofit2)
s0.paramsAIP.CopyFrom(paramsaip)
p0 = trdb2py.trading2_pb2.SimTradingParams(
    assets=[trdb2py.str2asset(asset)],
    startTs=tsStart,
    endTs=tsEnd,
    strategies=[s0],
    title='高点月定投',
) 
lstparams.append(p0)


buy0 = trdb2py.trading2_pb2.CtrlCondition(
    name='timestampex',
    int64Vals=lstlow,
)

s0 = trdb2py.trading2_pb2.Strategy(
    name="normal",
    asset=trdb2py.str2asset(asset),
)

s0.buy.extend([buy0])
#     s0.takeprofit.extend([takeprofit0])
s0.paramsBuy.CopyFrom(paramsbuy)
#     s0.paramsSell.CopyFrom(paramssell)
#     s0.paramsTakeProfit.CopyFrom(paramstakeprofit2)
s0.paramsAIP.CopyFrom(paramsaip)
p0 = trdb2py.trading2_pb2.SimTradingParams(
    assets=[trdb2py.str2asset(asset)],
    startTs=tsStart,
    endTs=tsEnd,
    strategies=[s0],
    title='低点月定投',
) 
lstparams.append(p0)

lstaippnl = trdb2py.simTradings(trdb2cfg, lstparams)

trdb2py.showPNLs(lstaippnl + [pnlBaseline], toImg=isStaticImg, width=width, height=height)